In [1]:
import numpy as np
import pandas as pd
import scipy
from scipy import stats

import dask.dataframe as dd
from pathlib import Path
import glob

import datetime as dt

import matplotlib.pyplot as plt
from matplotlib import colors
import soundfile as sf
import matplotlib.patches as patches

import re

In [2]:
import sys

sys.path.append("../src")

In [3]:
import data_handling as dh
import subsampling as ss
from core import SITE_NAMES, DC_COLOR_MAPPINGS, FREQ_GROUPS

from cli import get_file_paths
import plotting
import pipeline

In [4]:
type_key = 'LF1'
site_key = "Foliage"
cycle_lengths = [1800, 360]
percent_ons = [0.1667]
specific_dc_tag = "1800of1800"

In [5]:
pipeline_params = dict()
pipeline_params['assemble_location_summary'] = False
pipeline_params["read_csv"] = True
pipeline_params["save_activity_grid"] = False
pipeline_params["save_presence_grid"] = False
pipeline_params["save_dc_night_comparisons"] = False
pipeline_params["save_activity_dc_comparisons"] = False
pipeline_params["save_presence_dc_comparisons"] = False
pipeline_params["show_plots"] = False
pipeline_params["show_PST"] = True
pipeline_params

{'assemble_location_summary': False,
 'read_csv': True,
 'save_activity_grid': False,
 'save_presence_grid': False,
 'save_dc_night_comparisons': False,
 'save_activity_dc_comparisons': False,
 'save_presence_dc_comparisons': False,
 'show_plots': False,
 'show_PST': True}

In [6]:
data_params = dict()
data_params["site_name"] = SITE_NAMES[site_key]
data_params["site_tag"] = site_key
data_params["type_tag"] = type_key
data_params["cycle_lengths"] = cycle_lengths
data_params["percent_ons"] = percent_ons
dc_tags = ss.get_list_of_dc_tags(data_params["cycle_lengths"], data_params["percent_ons"])
data_params["dc_tags"] = dc_tags
data_params["cur_dc_tag"] = specific_dc_tag
data_params['resolution_in_min'] = '30'
data_params['recording_start'] = '02:00'
data_params['recording_end'] = '13:30'
data_params

{'site_name': 'Foliage',
 'site_tag': 'Foliage',
 'type_tag': 'LF1',
 'cycle_lengths': [1800, 360],
 'percent_ons': [0.1667],
 'dc_tags': ['1800of1800', '300of1800', '60of360'],
 'cur_dc_tag': '1800of1800',
 'resolution_in_min': '30',
 'recording_start': '02:00',
 'recording_end': '13:30'}

In [7]:
file_paths = get_file_paths(data_params)
file_paths

{'raw_SITE_folder': '/Users/adityakrishna/duty-cycle-investigation/src/../data/raw/Foliage',
 'SITE_folder': '/Users/adityakrishna/duty-cycle-investigation/src/../data/2022_bd2_summary/Foliage',
 'bd2_TYPE_SITE_YEAR': 'bd2__LF1Foliage_2022',
 'duty_cycled_folder': '/Users/adityakrishna/duty-cycle-investigation/src/../data/2022_bd2_summary/Foliage/duty_cycled',
 'dc_dets_TYPE_SITE_summary': 'dc_dets_LF1Foliage_summary',
 'dc_bouts_TYPE_SITE_summary': 'dc_bouts_LF1Foliage_summary',
 'dc_inds_TYPE_SITE_summary': 'dc_inds_LF1Foliage_summary',
 'simulated_schemes_folder': '/Users/adityakrishna/duty-cycle-investigation/src/../data/2022_bd2_summary/Foliage/duty_cycled/simulated_schemes',
 'figures_SITE_folder': '/Users/adityakrishna/duty-cycle-investigation/src/../figures/Foliage',
 'activity_det_comparisons_figname': 'activity_det_comparisons_per_dc_LF1Foliage',
 'dc_det_comparisons_figname': 'dc_det_comparisons_per_night_LF1Foliage',
 'activity_bout_comparisons_figname': 'activity_bout_comp

In [8]:
def assemble_initial_location_summary(data_params, file_paths, save=True):
    """
    Puts together all bd2 outputs in data/raw and converts detection start_times to datetime objects.
    Returns and saves a summary of bd2-detected bat calls within a desired frequency band.
    """

    location_df = dd.read_csv(f'{file_paths["raw_SITE_folder"]}/*.csv').compute()
    location_df['low_freq'] = location_df['low_freq'].astype('float')
    location_df['high_freq'] = location_df['high_freq'].astype('float')
    file_dts = pd.to_datetime(location_df['input_file'], format='%Y%m%d_%H%M%S', exact=False)
    anchor_start_times = file_dts + pd.to_timedelta(location_df['start_time'].values.astype('float64'), unit='S')
    anchor_end_times = file_dts + pd.to_timedelta(location_df['end_time'].values.astype('float64'), unit='S')

    location_df.insert(0, 'call_end_time', anchor_end_times)
    location_df.insert(0, 'call_start_time', anchor_start_times)
    location_df.insert(0, 'ref_time', anchor_start_times)
    location_df.insert(0, 'freq_group', '')

    groups = FREQ_GROUPS[data_params['site_tag']]
    blue_group = groups[list(groups.keys())[0]]
    red_group = groups[list(groups.keys())[1]]
    yellow_group = groups[list(groups.keys())[2]]

    call_is_yellow = (location_df['low_freq']>=yellow_group[0])&(location_df['high_freq']<=yellow_group[1])
    call_is_red = (location_df['low_freq']>=red_group[0])&(location_df['high_freq']<=red_group[1])
    call_is_blue = (location_df['low_freq']>=blue_group[0])&(location_df['high_freq']<=blue_group[1])

    location_df.loc[call_is_yellow, 'freq_group'] = 'HF2'
    location_df.loc[call_is_red&(~(call_is_yellow)), 'freq_group'] = 'HF1'
    location_df.loc[call_is_blue&(~(call_is_red | call_is_yellow)), 'freq_group'] = 'LF1'
    
    if data_params['type_tag'] != '':
        location_df = location_df.loc[location_df['freq_group']==data_params['type_tag']]


    return location_df

In [9]:
assemble_initial_location_summary(data_params, file_paths, save=False)

freq_group                   ref_time            call_start_time  \
0          LF1 2022-06-15 03:33:24.469500 2022-06-15 03:33:24.469500   
338        LF1 2022-06-15 04:42:22.783500 2022-06-15 04:42:22.783500   
339        LF1 2022-06-15 04:42:24.231500 2022-06-15 04:42:24.231500   
340        LF1 2022-06-15 04:42:24.705500 2022-06-15 04:42:24.705500   
357        LF1 2022-06-15 04:43:05.575500 2022-06-15 04:43:05.575500   
..         ...                        ...                        ...   
12         LF1 2022-10-17 08:00:51.110500 2022-10-17 08:00:51.110500   
13         LF1 2022-10-17 08:00:51.336500 2022-10-17 08:00:51.336500   
14         LF1 2022-10-17 08:00:51.550500 2022-10-17 08:00:51.550500   
15         LF1 2022-10-17 08:00:51.778500 2022-10-17 08:00:51.778500   
16         LF1 2022-10-17 08:00:52.248500 2022-10-17 08:00:52.248500   

                 call_end_time start_time            end_time  low_freq  \
0   2022-06-15 03:33:24.485600   204.4695            204.4856   18593.0   
338 2022-06-15 04:42:22.799900   742.7835            742.7999   22890.0   
339 2022-06-15 04:42:24.246800   744.2315            744.2468   22890.0   
340 2022-06-15 04:42:24.721700   744.7055            744.7217   22890.0   
357 2022-06-15 04:43:05.591400   785.5755            785.5914   24609.0   
..                         ...        ...                 ...       ...   
12  2022-10-17 08:00:51.125300    51.1105             51.1253   26328.0   
13  2022-10-17 08:00:51.351600    51.3365  51.351600000000005   26328.0   
14  2022-10-17 08:00:51.565000    51.5505              51.565   25468.0   
15  2022-10-17 08:00:51.793700    51.7785             51.7937   25468.0   
16  2022-10-17 08:00:52.263500    52.2485             52.2635   25468.0   

     high_freq         event              class class_prob det_prob  \
0      23399.0  Echolocation   Nyctalus noctula      0.399    0.544   
338    26704.0  Echolocation  Nyctalus leisleri       0.52      0.6   
339    28244.0  Echolocation  Nyctalus leisleri      0.555     0.66   
340    28061.0  Echolocation  Nyctalus leisleri      0.471    0.601   
357    29948.0  Echolocation  Nyctalus leisleri      0.328     0.53   
..         ...           ...                ...        ...      ...   
12     30370.0  Echolocation  Nyctalus leisleri       0.46    0.557   
13     29379.0  Echolocation  Nyctalus leisleri      0.543    0.608   
14     30578.0  Echolocation  Nyctalus leisleri      0.388    0.556   
15     29126.0  Echolocation  Nyctalus leisleri      0.529    0.607   
16     29590.0  Echolocation  Nyctalus leisleri      0.486      0.6   

    individual                                         input_file Site name  \
0           -1  /mnt/ubna_data_01/recover-20220616_unit2/20220...   Foliage   
338         -1  /mnt/ubna_data_01/recover-20220616_unit2/20220...   Foliage   
339         -1  /mnt/ubna_data_01/recover-20220616_unit2/20220...   Foliage   
340         -1  /mnt/ubna_data_01/recover-20220616_unit2/20220...   Foliage   
357         -1  /mnt/ubna_data_01/recover-20220616_unit2/20220...   Foliage   
..         ...                                                ...       ...   
12          -1  /mnt/ubna_data_02/recover-20221017/UBNA_008/20...   Foliage   
13          -1  /mnt/ubna_data_02/recover-20221017/UBNA_008/20...   Foliage   
14          -1  /mnt/ubna_data_02/recover-20221017/UBNA_008/20...   Foliage   
15          -1  /mnt/ubna_data_02/recover-20221017/UBNA_008/20...   Foliage   
16          -1  /mnt/ubna_data_02/recover-20221017/UBNA_008/20...   Foliage   

             Recover Folder SD Card  
0    recover-20220616_unit2      10  
338  recover-20220616_unit2      10  
339  recover-20220616_unit2      10  
340  recover-20220616_unit2      10  
357  recover-20220616_unit2      10  
..                      ...     ...  
12         recover-20221017       8  
13         recover-20221017       8  
14         recover-20221017       8  
15         recover-20221017       8  
16         recover

In [10]:
pd.read_csv(f'{file_paths["SITE_folder"]}/{file_paths["bd2_TYPE_SITE_YEAR"]}.csv', low_memory=False, index_col=0)

freq_group                       ref_time                call_start_time  \
0          LF1  2022-06-15 03:33:24.469500000  2022-06-15 03:33:24.469500000   
338        LF1  2022-06-15 04:42:22.783500000  2022-06-15 04:42:22.783500000   
339        LF1  2022-06-15 04:42:24.231500000  2022-06-15 04:42:24.231500000   
340        LF1  2022-06-15 04:42:24.705500000  2022-06-15 04:42:24.705500000   
357        LF1  2022-06-15 04:43:05.575500000  2022-06-15 04:43:05.575500000   
..         ...                            ...                            ...   
12         LF1  2022-10-17 08:00:51.110500000  2022-10-17 08:00:51.110500000   
13         LF1  2022-10-17 08:00:51.336500000  2022-10-17 08:00:51.336500000   
14         LF1  2022-10-17 08:00:51.550500000  2022-10-17 08:00:51.550500000   
15         LF1  2022-10-17 08:00:51.778500000  2022-10-17 08:00:51.778500000   
16         LF1  2022-10-17 08:00:52.248500000  2022-10-17 08:00:52.248500000   

                     call_end_time  start_time  end_time  low_freq  high_freq  \
0    2022-06-15 03:33:24.485600000    204.4695  204.4856   18593.0    23399.0   
338  2022-06-15 04:42:22.799900000    742.7835  742.7999   22890.0    26704.0   
339  2022-06-15 04:42:24.246800000    744.2315  744.2468   22890.0    28244.0   
340  2022-06-15 04:42:24.721700000    744.7055  744.7217   22890.0    28061.0   
357  2022-06-15 04:43:05.591400000    785.5755  785.5914   24609.0    29948.0   
..                             ...         ...       ...       ...        ...   
12   2022-10-17 08:00:51.125300000     51.1105   51.1253   26328.0    30370.0   
13   2022-10-17 08:00:51.351600000     51.3365   51.3516   26328.0    29379.0   
14   2022-10-17 08:00:51.565000000     51.5505   51.5650   25468.0    30578.0   
15   2022-10-17 08:00:51.793700000     51.7785   51.7937   25468.0    29126.0   
16   2022-10-17 08:00:52.263500000     52.2485   52.2635   25468.0    29590.0   

            event              class  class_prob  det_prob  individual  \
0    Echolocation   Nyctalus noctula       0.399     0.544          -1   
338  Echolocation  Nyctalus leisleri       0.520     0.600          -1   
339  Echolocation  Nyctalus leisleri       0.555     0.660          -1   
340  Echolocation  Nyctalus leisleri       0.471     0.601          -1   
357  Echolocation  Nyctalus leisleri       0.328     0.530          -1   
..            ...                ...         ...       ...         ...   
12   Echolocation  Nyctalus leisleri       0.460     0.557          -1   
13   Echolocation  Nyctalus leisleri       0.543     0.608          -1   
14   Echolocation  Nyctalus leisleri       0.388     0.556          -1   
15   Echolocation  Nyctalus leisleri       0.529     0.607          -1   
16   Echolocation  Nyctalus leisleri       0.486     0.600          -1   

                                            input_file Site name  \
0    /mnt/ubna_data_01/recover-20220616_unit2/20220...   Foliage   
338  /mnt/ubna_data_01/recover-20220616_unit2/20220...   Foliage   
339  /mnt/ubna_data_01/recover-20220616_unit2/20220...   Foliage   
340  /mnt/ubna_data_01/recover-20220616_unit2/20220...   Foliage   
357  /mnt/ubna_data_01/recover-20220616_unit2/20220...   Foliage   
..                                                 ...       ...   
12   /mnt/ubna_data_02/recover-20221017/UBNA_008/20...   Foliage   
13   /mnt/ubna_data_02/recover-20221017/UBNA_008/20...   Foliage   
14   /mnt/ubna_data_02/recover-20221017/UBNA_008/20...   Foliage   
15   /mnt/ubna_data_02/recover-20221017/UBNA_008/20...   Foliage   
16   /mnt/ubna_data_02/recover-20221017/UBNA_008/20...   Foliage   

             Recover Folder SD Card  
0    recover-20220616_unit2      10  
338  recover-20220616_unit2      10  
339  recover-20220616_unit2      10  
340  recover-20220616_unit2      10  
357  recover-20220616_unit2      10  
..                      ...     ...  
12         recover-20221017       8  
13         recover-20221017       8  
14         recover-202

In [11]:
def test_number_of_detections_less_than_max_per_30(num_of_detections, max_allowable_calls_per_30):
    assertion = (num_of_detections <= max_allowable_calls_per_30).values
    assert(not(False in assertion))

def construct_activity_arr_from_location_summary(location_df, dc_tag, file_paths, data_params):
    """
    Construct an activity summary for each date and time's number of detected calls. Only looking from 03:00 to 13:00 UTC.
    Will be used later to assembled an activity summary for each duty-cycling scheme to compare effects.
    """
    location_df.insert(0, 'call_durations', (location_df['call_end_time'] - location_df['call_start_time']))
    df_resampled_every_30 = location_df.resample(f"{data_params['resolution_in_min']}T", on='ref_time')
    shortest_call_per_30 = pd.to_numeric(df_resampled_every_30['call_durations'].min())/1e6
    max_allowable_calls_per_30 = np.abs(((int(data_params['resolution_in_min'])*60*60) / shortest_call_per_30))
    num_of_detections = df_resampled_every_30['ref_time'].count()
    test_number_of_detections_less_than_max_per_30(num_of_detections, max_allowable_calls_per_30)

    all_processed_filepaths = sorted(list(map(str, list(Path(f'{file_paths["raw_SITE_folder"]}').glob('*.csv')))))
    all_processed_datetimes = pd.to_datetime(all_processed_filepaths, format="%Y%m%d_%H%M%S", exact=False)
    col_name = f"Number_of_Detections ({dc_tag})"
    incomplete_activity_arr = pd.DataFrame(num_of_detections.values, index=num_of_detections.index, columns=[col_name])
    activity_arr = incomplete_activity_arr.reindex(index=all_processed_datetimes, fill_value=0).resample(f"{data_params['resolution_in_min']}T").first()
    activity_arr = activity_arr.between_time(data_params['recording_start'], data_params['recording_end'], inclusive='left')

    return pd.DataFrame(list(zip(activity_arr.index, activity_arr[col_name].values)), columns=["Date_and_Time_UTC", col_name])

In [12]:
def simulate_dutycycle_on_detections(location_df, dc_tag):
    """
    Simulates a provided duty-cycling scheme on the provided location summary of concatenated bd2 outputs.
    """

    cycle_length = int(dc_tag.split('of')[1])
    time_on = int(dc_tag.split('of')[0])

    location_df['ref_time'] = pd.DatetimeIndex(location_df['ref_time'])
    location_df['call_end_time'] = pd.DatetimeIndex(location_df['call_end_time'])
    location_df['call_start_time'] = pd.DatetimeIndex(location_df['call_start_time'])
    
    resampled_df = location_df.resample(f'{cycle_length}S', on='ref_time')
    location_df['ref_time'] = resampled_df['ref_time'].transform(lambda x: x.name)
    location_df.insert(0, 'end_time_wrt_ref', (location_df['call_end_time'] - location_df['ref_time']).dt.total_seconds())
    location_df.insert(0, 'start_time_wrt_ref', (location_df['call_start_time'] - location_df['ref_time']).dt.total_seconds())

    dc_applied_df = location_df.loc[(location_df['end_time_wrt_ref'] <= time_on)&(location_df['start_time_wrt_ref'] >= 0)]
    test_for_last_call_within_period(dc_applied_df, cycle_length, time_on)

    return dc_applied_df

def test_for_last_call_within_period(dc_applied_df, cycle_length, time_on):
    calls_grouped_per_cycle = dc_applied_df.resample(f'{cycle_length}S', on='ref_time')
    on_periods = (calls_grouped_per_cycle['ref_time'].first() + pd.to_timedelta(f'{time_on}S')).dropna()
    last_calls_in_periods = (calls_grouped_per_cycle['call_end_time'].max().dropna()) <= on_periods
    first_calls_in_periods = (calls_grouped_per_cycle['call_start_time'].min().dropna()) >= on_periods.index
    assert(not(False in first_calls_in_periods) and not(False in last_calls_in_periods))

def prepare_summary_for_plotting_with_duty_cycle(file_paths, dc_tag):
    """
    Generates a duty-cycled location summary of concatenated bd2 outputs for measuring effects of duty-cycling.
    """

    location_df = pd.read_csv(f'{file_paths["SITE_folder"]}/{file_paths["bd2_TYPE_SITE_YEAR"]}.csv', low_memory=False, index_col=0)
    plottable_location_df = simulate_dutycycle_on_detections(location_df, dc_tag)

    return plottable_location_df

In [13]:
activity_dets_arr = pd.DataFrame()

for dc_tag in data_params['dc_tags']:
    location_df = prepare_summary_for_plotting_with_duty_cycle(file_paths, dc_tag)
    dc_dets = construct_activity_arr_from_location_summary(location_df, dc_tag, file_paths, data_params)
    dc_dets = dc_dets.set_index("Date_and_Time_UTC")
    activity_dets_arr = pd.concat([activity_dets_arr, dc_dets], axis=1)
activity_dets_arr

Number_of_Detections (1800of1800)  \
Date_and_Time_UTC                                        
2022-06-15 02:00:00                                0.0   
2022-06-15 02:30:00                                0.0   
2022-06-15 03:00:00                                0.0   
2022-06-15 03:30:00                                1.0   
2022-06-15 04:00:00                                0.0   
...                                                ...   
2022-10-17 11:00:00                                0.0   
2022-10-17 11:30:00                                0.0   
2022-10-17 12:00:00                                0.0   
2022-10-17 12:30:00                                0.0   
2022-10-17 13:00:00                                0.0   

                     Number_of_Detections (300of1800)  \
Date_and_Time_UTC                                       
2022-06-15 02:00:00                               0.0   
2022-06-15 02:30:00                               0.0   
2022-06-15 03:00:00                               0.0   
2022-06-15 03:30:00                               1.0   
2022-06-15 04:00:00                               0.0   
...                                               ...   
2022-10-17 11:00:00                               0.0   
2022-10-17 11:30:00                               0.0   
2022-10-17 12:00:00                               0.0   
2022-10-17 12:30:00                               0.0   
2022-10-17 13:00:00                               0.0   

                     Number_of_Detections (60of360)  
Date_and_Time_UTC                                    
2022-06-15 02:00:00                             0.0  
2022-06-15 02:30:00                             0.0  
2022-06-15 03:00:00                             0.0  
2022-06-15 03:30:00                             0.0  
2022-06-15 04:00:00                             0.0  
...                                             ...  
2022-10-17 11:00:00                             0.0  
2022-10-17 11:30:00                             0.0  
2022-10-17 12:00:00                             0.0  
2022-10-17 12:30:00                             0.0  
2022-10-17 13:00:00                             0.0  

[2875 rows x 3 columns]

In [14]:
activity_dets_arr[60:70]

Number_of_Detections (1800of1800)  \
Date_and_Time_UTC                                        
2022-06-17 09:00:00                              100.0   
2022-06-17 09:30:00                               22.0   
2022-06-17 10:00:00                              191.0   
2022-06-17 10:30:00                               10.0   
2022-06-17 11:00:00                               46.0   
2022-06-17 11:30:00                                0.0   
2022-06-17 12:00:00                                0.0   
2022-06-17 12:30:00                                0.0   
2022-06-17 13:00:00                                0.0   
2022-06-18 02:00:00                                NaN   

                     Number_of_Detections (300of1800)  \
Date_and_Time_UTC                                       
2022-06-17 09:00:00                               5.0   
2022-06-17 09:30:00                               0.0   
2022-06-17 10:00:00                               5.0   
2022-06-17 10:30:00                               9.0   
2022-06-17 11:00:00                               0.0   
2022-06-17 11:30:00                               0.0   
2022-06-17 12:00:00                               0.0   
2022-06-17 12:30:00                               0.0   
2022-06-17 13:00:00                               0.0   
2022-06-18 02:00:00                               NaN   

                     Number_of_Detections (60of360)  
Date_and_Time_UTC                                    
2022-06-17 09:00:00                            23.0  
2022-06-17 09:30:00                             0.0  
2022-06-17 10:00:00                            28.0  
2022-06-17 10:30:00                             0.0  
2022-06-17 11:00:00                             7.0  
2022-06-17 11:30:00                             0.0  
2022-06-17 12:00:00                             0.0  
2022-06-17 12:30:00                             0.0  
2022-06-17 13:00:00                             0.0  
2022-06-18 02:00:00                             NaN

In [15]:
activity_arr = pipeline.run_for_dets(data_params, pipeline_params, file_paths)

In [16]:
dh.construct_activity_grid_for_number_of_dets(activity_arr, "1800of1800")

Date (UTC)  06/15/22  06/16/22  06/17/22  06/18/22  06/19/22  06/20/22  \
Time (UTC)                                                               
02:00            0.0       0.0       2.0       NaN       2.0       NaN   
02:30            0.0       0.0       0.0       NaN       1.0       NaN   
03:00            0.0       5.0       0.0       NaN       0.0       NaN   
03:30            1.0       1.0       0.0       NaN       0.0       NaN   
04:00            0.0      87.0       0.0       NaN       0.0       NaN   
04:30          292.0    4317.0    2432.0       NaN      37.0       NaN   
05:00           72.0    1712.0    1855.0       NaN     332.0       NaN   
05:30           63.0    1759.0    2040.0       NaN     594.0       NaN   
06:00           93.0     259.0     107.0       NaN       NaN       NaN   
06:30           23.0     144.0     196.0       NaN       NaN       NaN   
07:00           20.0      60.0      98.0       NaN       NaN       NaN   
07:30           13.0     157.0       6.0       NaN       NaN       NaN   
08:00            8.0      89.0      58.0       NaN       NaN       NaN   
08:30           41.0     114.0      76.0       NaN       NaN       NaN   
09:00            4.0      19.0     100.0       NaN       NaN       NaN   
09:30            5.0     303.0      22.0       NaN       NaN       NaN   
10:00           22.0     318.0     191.0       NaN       NaN       NaN   
10:30            9.0      10.0      10.0       NaN       NaN       NaN   
11:00           64.0      13.0      46.0       NaN       NaN       NaN   
11:30            0.0       0.0       0.0       NaN       NaN       NaN   
12:00            0.0       0.0       0.0       NaN       NaN       NaN   
12:30            0.0       0.0       0.0       NaN       NaN       NaN   
13:00            2.0       0.0       0.0       NaN       NaN       NaN   

Date (UTC)  06/21/22  06/22/22  06/23/22  06/24/22  ...  10/08/22  10/09/22  \
Time (UTC)                                          ...                       
02:00            1.0       NaN       0.0       0.0  ...      18.0       6.0   
02:30            1.0       NaN       1.0       0.0  ...      20.0       9.0   
03:00            0.0       NaN       0.0       0.0  ...       0.0      31.0   
03:30            0.0       NaN       0.0       1.0  ...       0.0       1.0   
04:00            1.0       NaN       0.0       0.0  ...       2.0       3.0   
04:30         2195.0       NaN    1522.0    2375.0  ...       2.0       3.0   
05:00         2344.0       NaN      20.0    1408.0  ...      10.0       0.0   
05:30         1129.0       NaN     142.0     357.0  ...       3.0       5.0   
06:00          208.0       NaN      27.0     137.0  ...       3.0       1.0   
06:30           85.0       NaN      69.0      40.0  ...       8.0       7.0   
07:00           66.0       NaN      32.0      13.0  ...       1.0       2.0   
07:30           30.0       NaN      30.0      22.0  ...       2.0       6.0   
08:00           50.0       NaN      34.0       6.0  ...       7.0       6.0   
08:30           33.0       NaN      17.0       4.0  ...       6.0       6.0   
09:00           61.0       NaN      84.0      11.0  ...      22.0       1.0   
09:30            0.0       NaN       7.0      29.0  ...       1.0       0.0   
10:00           14.0       NaN      41.0     151.0  ...       5.0       5.0   
10:30           39.0       NaN       5.0      27.0  ...       6.0       3.0   
11:00           38.0       NaN      33.0       8.0  ...       1.0       5.0   
11:30          125.0       NaN       0.0       0.0  ...       0.0       5.0   
12:00            0.0       NaN       0.0       0.0  ...       4.0       4.0   
12:30            0.0       NaN       0.0       1.0  ...       7.0       3.0   
13:00            1.0       NaN       3.0       1.0  ...       6.0       6.0   

Date (UTC)  10/10/22  10/11/22  10/12/22  10/13/22  10/14/22  10/15/22  \
Time (UTC)                                                               
02:00            6.0     

In [17]:
plotting.plot_activity_grid_for_dets(dh.construct_activity_grid_for_number_of_dets(activity_arr, data_params["cur_dc_tag"]), data_params, pipeline_params, file_paths)

In [18]:
plotting.plot_dc_det_activity_comparisons_per_scheme(activity_arr, data_params, pipeline_params, file_paths)

In [19]:
# plotting.plot_dc_presence_comparisons_per_scheme(activity_arr, data_params, pipeline_params, file_paths)

In [20]:
# pipeline.plot_dets(activity_arr, data_params, pipeline_params, file_paths)